# Capstone Project - The Battle of the Neighborhoods
### Applied Data Science Capstone by IBM/Coursera

## Introduction: Business Problem

Before you move to  a city, it can be hard to tell the character of individual cities. The sheer size and polpulation of the Indian cities can be overwhelming, and for some it might be tempting to paint all busy centres with the same brush. But in reality, you can have drastically different experiences depending on where you visit. Mumbai and Delhi epitomise this: one’s a modern, cosmopolitan and commercial centre while the other, in places, feels like a gateway to a bygone era. Here, we let Data decide the similar neighborhoods based on the surrounding amenities between **Delhi and Mumbai**.

We will use our data science powers to generate a few most promissing neighborhoods based on similarity between two cities. Advantages of each area will then be clearly expressed so that best possible final location can be chosen by stakeholders.

## Data

Based on definition of our problem, factors that will influence our decission are:
* number of existing amenities in the neighborhood (any type of restaurant)

For this study, we needed data about neighborhoods in each of these metro cities.


**Mumbai** : https://www.mapsofindia.com/pincode/india/maharashtra/mumbai/

**Delhi**  : https://www.movingsolutions.in/blog/2020/02/05/pin-codes-of-delhi-locations/ 

Following data sources will be needed to extract/generate the required information:
* number of amenities and their type and location in every neighborhood will be obtained using **Foursquare API**
* coordinate of locations will be obtained using **Geopy Geocode**

In [1]:
import numpy as np

import pandas as pd
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json 

#!conda install -c conda-forge geopy --yes 
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes 
import folium # map rendering library

### Web Scrapping for Mumbai neighborhood data fetching

In [2]:
table_m = pd.read_html("https://www.mapsofindia.com/pincode/india/maharashtra/mumbai/",header=0,index_col=0)
Borough = ['Mumbai']

In [3]:
mumbai = table_m[0]
mumbai = mumbai.reset_index()
mumbai.rename(columns = {'Pincode Details':'Neighborhood','Pincode Details.1':'Pincode','Pincode Details.2': 'State','Pincode Details.3': 'District'}, inplace = True)    
mumbai=mumbai.drop(columns=[ 'State'])
mumbai=mumbai.drop(mumbai.index[0])
mumbai.head()

Neighborhood Pincode District
1  A I staff colony  400029   Mumbai
2  Aareymilk Colony  400065   Mumbai
3          Agripada  400011   Mumbai
4           Airport  400099   Mumbai
5          Ambewadi  400004   Mumbai

### Neighborhood Candidates

Let's create latitude & longitude coordinates for centroids of our candidate neighborhoods. We will create a grid of cells covering our area of interest which is aprox. 12x12 killometers centered around Berlin city center.

Let's first find the latitude & longitude of Berlin city center, using specific, well known address and Google Maps geocoding API.

In [4]:
# define a sample to get coordinates
locator = Nominatim(user_agent='myGeocoder')
location = locator.geocode('Borivali', 'Mumbai')
print('latitude = {}, longitude = {}'.format(location.latitude, location.longitude))

latitude = 19.229068, longitude = 72.8573628


In [5]:
# define a function to get coordinates
def get_latlng(Neighborhood):
    # initialize your variable to None
    lat_lng_coords = None
    lat_lng_coords = locator.geocode(Neighborhood)
    
    if(lat_lng_coords is None):
        for i in range(5):
            lat_lng_coords = locator.geocode(Neighborhood)
    if(lat_lng_coords is None):
        lat_lng_coords = 'Nan'
    return lat_lng_coords

In [6]:
# call the function to get the coordinates, store in a new list using list comprehension
coords = [ get_latlng('{},Mumbai'.format(Neighborhood)) for Neighborhood in mumbai["Neighborhood"].tolist() ]

In [7]:
latitude = []
longitude = []
for data in coords:
    if data != 'Nan':
        latitude.append(data.latitude)
        longitude.append(data.longitude)
    else :
        latitude.append(0)
        longitude.append(0)

In [8]:
mumbai['Latitude']=latitude
mumbai['Longitude']=longitude
mumbai = mumbai[mumbai['Latitude'] != 0]
mumbai.head()

Neighborhood Pincode District   Latitude  Longitude
3      Agripada  400011   Mumbai  18.975302  72.824898
4       Airport  400099   Mumbai  19.090201  72.863808
5      Ambewadi  400004   Mumbai  19.186776  72.859313
6       Andheri  400053   Mumbai  19.119698  72.846420
7  Andheri East  400069   Mumbai  19.115883  72.854202

### Web Scrapping for Mumbai neighborhood data fetching¶

In [9]:
tables_d = pd.read_html("https://www.movingsolutions.in/blog/2020/02/05/pin-codes-of-delhi-locations/",header=0,index_col=0)
Borough_d = ['East Delhi', 'West delhi', 'South Delhi', 'North Delhi', 'New Delhi', 'Central Delhi', 'West Delhi', 'South West Delhi']

In [10]:
for i in range(len(Borough_d)):
    tables_d[i]['District']=Borough_d[i]  
Delhi = tables_d[0]    
for j in range(len(Borough_d)-1):
    Delhi = pd.concat([Delhi, tables_d[j+1]])

Delhi = Delhi.reset_index()
Delhi.rename(columns = {'Location':'Neighborhood', 'Pin code':'Pincode', 'District':'Borough'}, inplace = True)    
Delhi.head()

Neighborhood  Pincode     Borough
0   Anand Vihar   110092  East Delhi
1    Azad Nagar   110051  East Delhi
2      Babarpur   110032  East Delhi
3  Balbir Nagar   110032  East Delhi
4   Bhajan Pura   110053  East Delhi

In [11]:
location = locator.geocode('adarsh nagar,delhi, india')
print('Latitude = {}, Longitude = {}'.format(location.latitude, location.longitude))

Latitude = 28.7144008, Longitude = 77.1672884


In [12]:
# call the function to get the coordinates, store in a new list using list comprehension
coords_d = [ get_latlng('{}, Delhi, india'.format(Neighborhood)) for Neighborhood in Delhi["Neighborhood"].tolist() ]

In [13]:
latitude = []
longitude = []
for data in coords_d:
    if data != 'Nan':
        latitude.append(data.latitude)
        longitude.append(data.longitude)
    else :
        latitude.append(0)
        longitude.append(0)

In [14]:
Delhi['Latitude']=latitude
Delhi['Longitude']=longitude

In [15]:
Delhi = Delhi[Delhi['Latitude'] != 0]
Delhi.head()

Neighborhood  Pincode     Borough   Latitude  Longitude
0       Anand Vihar   110092  East Delhi  28.641115  77.312502
1        Azad Nagar   110051  East Delhi  28.662682  77.279515
2          Babarpur   110032  East Delhi  28.687431  77.279755
3      Balbir Nagar   110032  East Delhi  28.683790  77.290754
5  Bhola Nath nagar   110032  East Delhi  28.669127  77.285241

## Merging Delhi and Mumbai dataframes

In [16]:
data=pd.concat([mumbai,Delhi], axis=0 )
data.drop(['Borough', 'District', 'Pincode'],axis=1,inplace=True)
data.head()

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:1: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  if __name__ == '__main__':


Latitude  Longitude  Neighborhood
3  18.975302  72.824898      Agripada
4  19.090201  72.863808       Airport
5  19.186776  72.859313      Ambewadi
6  19.119698  72.846420       Andheri
7  19.115883  72.854202  Andheri East

### obtaining Geocodes of Mumbai for creating a map

In [17]:
address = 'Mumbai, IN'

location = locator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Mumbai are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Mumbai are 18.9387711, 72.8353355.


In [18]:
map = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for Latitude, Longitude,  Neighborhood in zip(data['Latitude'], data['Longitude'], data['Neighborhood']):
    label = '{}'.format(Neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [Latitude, Longitude],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map) 
    
map

Foursquare

Now that we have our location candidates, let's use Foursquare API to get info on Amenities in each neighborhood.

In [19]:
# The code was removed by Watson Studio for sharing.

Your credentails:
CLIENT_ID: WDYUDPBSNVHNSR3NNV54QXP4GSSMGFF0Z5XMRWFPEW2UFL3T
CLIENT_SECRET:YH0RSL4NX0PRPVCJPTCSHPNH3QCOBLPRZHGXKZ0YKPHAZQFS


In [20]:
#Let's get the geographical coordinates of Anand Vihar
neighborhood_latitude = data.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = data.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name = data.loc[0, 'Neighborhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Anand Vihar are 28.641115, 77.3125024.


In [21]:
LIMIT = 100
radius = 1000
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)

In [22]:
results = requests.get(url).json()

In [23]:
#let's borrow the get_category_type function from the Foursquare lab. function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [24]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name     categories        lat        lng
0            PVR EDM  Movie Theater  28.641323  77.317026
1          Pizza Hut    Pizza Place  28.641347  77.317054
2    Barista Lavazza           Café  28.646416  77.320005
3  Big Cinemas, Imax      Multiplex  28.645940  77.319942
4   Lemon Tree Hotel          Hotel  28.641373  77.316549

In [25]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))


15 venues were returned by Foursquare.


## Methodology

The deciding factor for most would be on how lively, supportive, vibrant and unique each of the cities can be when compared to each other. The business problem in this study assumes that people who would be interested in this study are those who would like to create a projection of potential life and activities in these metro city neighborhoods if the subject moves to live in one of them. The decision to choose one over the other would depend on popular venues in the neighborhoods in each of these metro cities.

In [26]:
def getNearbyVenues(names, latitudes, longitudes, radius=300):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [28]:
all_venues = getNearbyVenues(names=data['Neighborhood'],
                   latitudes=data['Latitude'],
                   longitudes=data['Longitude']
                 )

Agripada
Airport
Ambewadi
Andheri
Andheri East
Andheri Railway station
Antop Hill
Asvini
Azad Nagar
B P t colony
B.N. bhavan
B.P.lane
Bandra West
Bandra(east)
Bangur Nagar
Bazargate
Best Staff colony
Bharat Nagar
Bhawani Shankar
Bhawani Shankar rd
Borivali
Borivali East
Central Building
Century Mill
Chakala Midc
Chamarbaug
Charkop
Charni Road
Chinchbunder
Chinchpokli
Churchgate
Colaba
Cotton Exchange
Cumballa Hill
Dadar
Dadar Colony
Dahisar
Danda
Daulat Nagar
Delisle Road
Dharavi
Dharavi Road
Dockyard Road
Dr Deshmukh marg
Falkland Road
Girgaon
Gokhale Road
Goregaon
Goregaon East
Government Colony
Gowalia Tank
Grant Road
Haines Road
Hanuman Road
Irla
Ins Hamla
International Airport
J.B. nagar
J.J.hospital
Jacob Circle
Jogeshwari East
Jogeshwari West
Juhu
Kalbadevi
Kamathipura
Kandivali East
Kandivali West
Ketkipada
Kharodi
Kherwadi
Kidwai Nagar
Lal Baug
Liberty Garden
M A marg
M.P.t.
Madh
Madhavbaug
Mahim
Mahim East
Malabar Hill
Malad
Malad East
Mandapeshwar
Mandvi
Mantralaya
Marine Li

In [29]:
all_venues.shape

(1870, 7)

In [30]:

all_venues.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0     Agripada              18.975302               72.824898   
1     Agripada              18.975302               72.824898   
2     Agripada              18.975302               72.824898   
3     Agripada              18.975302               72.824898   
4     Agripada              18.975302               72.824898   

                      Venue  Venue Latitude  Venue Longitude Venue Category  
0                   Celejor       18.975844        72.823679         Bakery  
1           cafe coffee day       18.976988        72.824051    Coffee Shop  
2              Baby gardens       18.973466        72.824510         Garden  
3        YMCA Swimming Pool       18.974498        72.824721           Pool  
4  YMCA Working Mens Hostel       18.973614        72.824427         Hostel

In [31]:
all_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                                    
Agripada                                     6                       6      6   
Airport                                      4                       4      4   
Alaknanda                                    4                       4      4   
Ali                                          5                       5      5   
Aliganj                                      4                       4      4   
Amar Colony                                  5                       5      5   
Ambewadi                                     3                       3      3   
Anand Parbat                                 2                       2      2   
Anand Vihar                                  2                       2      2   
Andheri                                      6                       6      6   
Andheri East                                12                      12     12   
Andheri Railway station                      6                       6      6   
Antop Hill                                   4                       4      4   
Aps Colony                                   1                       1      1   
Ashok Nagar                                  1                       1      1   
Ashok Vihar                                  1                       1      1   
Azad Nagar                                   9                       9      9   
B.P.lane                                    48                      48     48   
Badarpur                                     2                       2      2   
Bakkarwala                                   1                       1      1   
Bandra West                                 16                      16     16   
Bandra(east)                                 6                       6      6   
Bangur Nagar                                 2                       2      2   
Bank Street                                  4                       4      4   
Baroda House                                 1                       1      1   
Barwala                                      1                       1      1   
Bazar Road                                   4                       4      4   
Bazargate                                   41                      41     41   
Begumpur                                     7                       7      7   
Bengali Market                              10                      10     10   
Bhalaswa                                     1                       1      1   
Bharat Nagar                                 1                       1      1   
Bhawani Shankar                              4                       4      4   
Bhawani Shankar rd                          10                      10     10   
Bhola Nath nagar                             1                       1      1   
Birla Lines                                  2                       2      2   
Borivali                                     8                       8      8   
Central Building                             9                       9      9   
Century Mill                                 1                       1      1   
Chakala Midc                                 4                       4      4   
Chamarbaug                                   4                       4      4   
Chand Nagar                                  3                       3      3   
Chand Pur                                    2                       2      2   
Chandni Chowk                               14                      14     14   
Charkop                                      4                       4      4   
Charni Road                                 16                      16     16   
Chattarpur                                   3                       3      3   
Chaukhandi                                   4          

In [32]:
print('There are {} uniques categories.'.format(len(all_venues['Venue Category'].unique())))

There are 216 uniques categories.


In [33]:
# one hot encoding
all_onehot = pd.get_dummies(all_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
all_onehot['Neighborhood'] = all_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [all_onehot.columns[-1]] + list(all_onehot.columns[:-1])
all_onehot = all_onehot[fixed_columns]

all_onehot.head()

Neighborhood  ATM  Accessories Store  Afghan Restaurant  Airport  \
0     Agripada    0                  0                  0        0   
1     Agripada    0                  0                  0        0   
2     Agripada    0                  0                  0        0   
3     Agripada    0                  0                  0        0   
4     Agripada    0                  0                  0        0   

   Airport Food Court  Airport Gate  Airport Lounge  Airport Service  \
0                   0             0               0                0   
1                   0             0               0                0   
2                   0             0               0                0   
3                   0             0               0                0   
4                   0             0               0                0   

   Airport Terminal  American Restaurant  Antique Shop  Arcade  Art Gallery  \
0                 0                    0             0       0            0   
1                 0                    0             0       0            0   
2                 0                    0             0       0            0   
3                 0                    0             0       0            0   
4                 0                    0             0       0            0   

   Art Museum  Arts & Crafts Store  Asian Restaurant  Astrologer  \
0           0                    0                 0           0   
1           0                    0                 0           0   
2           0                    0                 0           0   
3           0                    0                 0           0   
4           0                    0                 0           0   

   Athletics & Sports  Auto Workshop  BBQ Joint  Bagel Shop  Bakery  Bank  \
0                   0              0          0           0       1     0   
1                   0              0          0           0       0     0   
2                   0              0          0           0       0     0   
3                   0              0          0           0       0     0   
4                   0              0          0           0       0     0   

   Bar  Basketball Court  Beach  Bed & Breakfast  Beer Garden  \
0    0                 0      0                0            0   
1    0                 0      0                0            0   
2    0                 0      0                0            0   
3    0                 0      0                0            0   
4    0                 0      0                0            0   

   Bengali Restaurant  Big Box Store  Bike Rental / Bike Share  Bistro  \
0                   0              0                         0       0   
1                   0              0                         0       0   
2                   0              0                         0       0   
3                   0              0                         0       0   
4                   0              0                         0       0   

   Boat or Ferry  Bookstore  Boutique  Bowling Alley  Breakfast Spot  Brewery  \
0              0          0         0              0               0        0   
1              0          0         0              0               0        0   
2              0          0         0              0               0        0   
3              0          0         0              0               0        0   
4              0          0         0              0               0        0   

   Buffet  Burger Joint  Burrito Place  Bus Station  Bus Stop  \
0       0             0              0            0         0   
1       0             0              0            0         0   
2       0             0              0            0         0   
3       0             0              0            0         0   
4       0             0              0            0         0   

   Business Service  Cafeteria  Café  Camera Store  Candy Store  Castle  \
0           

In [34]:
all_onehot.shape

(1870, 217)

In [35]:
all_grouped = all_onehot.groupby('Neighborhood').mean().reset_index()
all_grouped

Neighborhood       ATM  Accessories Store  Afghan Restaurant  \
0                   Agripada  0.000000               0.00           0.000000   
1                    Airport  0.000000               0.00           0.000000   
2                  Alaknanda  0.000000               0.00           0.000000   
3                        Ali  0.000000               0.00           0.000000   
4                    Aliganj  0.000000               0.00           0.000000   
5                Amar Colony  0.000000               0.00           0.000000   
6                   Ambewadi  0.000000               0.00           0.000000   
7               Anand Parbat  0.500000               0.00           0.000000   
8                Anand Vihar  0.000000               0.00           0.000000   
9                    Andheri  0.000000               0.00           0.000000   
10              Andheri East  0.000000               0.00           0.000000   
11   Andheri Railway station  0.000000               0.00           0.000000   
12                Antop Hill  0.000000               0.00           0.000000   
13                Aps Colony  0.000000               0.00           0.000000   
14               Ashok Nagar  0.000000               0.00           0.000000   
15               Ashok Vihar  0.000000               0.00           0.000000   
16                Azad Nagar  0.000000               0.00           0.000000   
17                  B.P.lane  0.000000               0.00           0.000000   
18                  Badarpur  0.000000               0.00           0.000000   
19                Bakkarwala  1.000000               0.00           0.000000   
20               Bandra West  0.000000               0.00           0.000000   
21              Bandra(east)  0.000000               0.00           0.000000   
22              Bangur Nagar  0.000000               0.00           0.000000   
23               Bank Street  0.000000               0.00           0.000000   
24              Baroda House  0.000000               0.00           0.000000   
25                   Barwala  1.000000               0.00           0.000000   
26                Bazar Road  0.000000               0.00           0.000000   
27                 Bazargate  0.000000               0.00           0.000000   
28                  Begumpur  0.000000               0.00           0.000000   
29            Bengali Market  0.000000               0.00           0.000000   
30                  Bhalaswa  0.000000               0.00           0.000000   
31              Bharat Nagar  0.000000               0.00           0.000000   
32           Bhawani Shankar  0.000000               0.00           0.000000   
33        Bhawani Shankar rd  0.000000               0.00           0.000000   
34          Bhola Nath nagar  1.000000               0.00           0.000000   
35               Birla Lines  0.500000               0.00           0.000000   
36                  Borivali  0.000000               0.00           0.000000   
37          Central Building  0.000000               0.00           0.000000   
38              Century Mill  0.000000               0.00           0.000000   
39              Chakala Midc  0.000000               0.00           0.000000   
40                Chamarbaug  0.000000               0.00           0.000000   
41               Chand Nagar  0.666667               0.00           0.000000   
42                 Chand Pur  0.000000               0.00           0.000000   
43             Chandni Chowk  0.000000               0.00           0.000000   
44                   Charkop  0.000000               0.00           0.000000   
45               Charni Road  0.000000               0.00           0.000000   
46                Chattarpur  0.333333               0.00           0.000000   
47                Chaukhandi  0.000000               0.00           0.000000   
48              Chawri Bazar  0.000000               0.00           0.000000   
49              

## Cluster the neighbourhoods in Mumbai based on the similarity of top common venues

In [36]:
num_top_venues = 5

for hood in all_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp =  all_grouped[all_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Agripada----
         venue  freq
0       Hostel  0.17
1  Coffee Shop  0.17
2         Pool  0.17
3         Bank  0.17
4       Bakery  0.17


----Airport----
             venue  freq
0          Airport  0.50
1  Airport Service  0.25
2    Jewelry Store  0.25
3              ATM  0.00
4    Moving Target  0.00


----Alaknanda----
                venue  freq
0         Coffee Shop  0.25
1   Food & Drink Shop  0.25
2  Chinese Restaurant  0.25
3        Burger Joint  0.25
4                 ATM  0.00


----Ali----
               venue  freq
0  Indian Restaurant   0.4
1             Hostel   0.2
2              Hotel   0.2
3      Movie Theater   0.2
4                ATM   0.0


----Aliganj----
               venue  freq
0  Indian Restaurant  0.50
1             Bakery  0.25
2        Record Shop  0.25
3                ATM  0.00
4      Moving Target  0.00


----Amar Colony----
               venue  freq
0        Coffee Shop   0.2
1             Market   0.2
2  Indian Restaurant   0.2
3       Dance S

In [37]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [38]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = all_grouped['Neighborhood']

for ind in np.arange(all_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(all_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0     Agripada                Garden           Coffee Shop   
1      Airport               Airport       Airport Service   
2    Alaknanda           Coffee Shop          Burger Joint   
3          Ali     Indian Restaurant                Hostel   
4      Aliganj     Indian Restaurant           Record Shop   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0                Hostel                  Bank                Bakery   
1         Jewelry Store           Yoga Studio    Dim Sum Restaurant   
2    Chinese Restaurant     Food & Drink Shop        Farmers Market   
3                 Hotel         Movie Theater           Yoga Studio   
4                Bakery          Dessert Shop        Farmers Market   

  6th Most Common Venue 7th Most Common Venue  8th Most Common Venue  \
0                  Pool          Dessert Shop                   Farm   
1  Fast Food Restaurant        Farmers Market                   Farm   
2                  Farm           Event Space  Entertainment Service   
3          Dessert Shop        Farmers Market                   Farm   
4                  Farm           Event Space  Entertainment Service   

  9th Most Common Venue 10th Most Common Venue  
0           Event Space  Entertainment Service  
1           Event Space  Entertainment Service  
2     Electronics Store         Duty-free Shop  
3           Event Space  Entertainment Service  
4     Electronics Store         Duty-free Shop

In [39]:
# set number of clusters
kclusters = 5

all_grouped_clustering = all_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(all_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_

array([0, 0, 0, 3, 3, 4, 3, 1, 0, 0, 0, 0, 3, 3, 0, 0, 0, 4, 2, 1, 4, 3,
       0, 0, 3, 1, 0, 0, 4, 4, 0, 0, 3, 0, 1, 3, 0, 4, 0, 0, 3, 1, 0, 3,
       4, 0, 1, 4, 0, 0, 4, 0, 0, 4, 0, 4, 0, 4, 4, 0, 3, 4, 4, 0, 0, 0,
       0, 2, 3, 0, 0, 0, 0, 0, 3, 0, 4, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0,
       0, 0, 0, 0, 3, 0, 0, 0, 0, 4, 0, 3, 0, 0, 0, 3, 0, 3, 0, 0, 0, 3,
       0, 0, 0, 0, 0, 4, 0, 4, 3, 0, 3, 0, 1, 3, 4, 0, 3, 0, 4, 0, 0, 0,
       4, 1, 4, 3, 3, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 3, 4, 0, 0, 3, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 3, 4, 1, 3, 2, 0, 3, 3, 3, 4, 0, 0,
       3, 4, 0, 0, 1, 3, 3, 4, 4, 0, 0, 0, 0, 0, 0, 4, 4, 0, 0, 3, 4, 0,
       0, 4, 2, 0, 3, 4, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 4, 0, 0, 0,
       1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 4, 0, 0, 0, 3, 4, 4, 0, 4, 0, 0,
       2, 3, 3, 4, 0, 0, 0, 0, 0, 0, 3, 3, 0, 1, 3, 1, 3, 4, 0, 0, 0, 3,
       0, 0, 4, 0, 4, 4, 4, 0, 0, 4, 3, 4, 3, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       3, 0, 0, 0, 4, 0, 1, 0, 4, 0, 0, 0, 0, 0, 0,

In [41]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels',kmeans.labels_)

In [42]:
all_merged =data
# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
all_merged = all_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')
all_merged.head() # check the last columns!

Latitude  Longitude  Neighborhood  Cluster Labels 1st Most Common Venue  \
3  18.975302  72.824898      Agripada             0.0                Garden   
4  19.090201  72.863808       Airport             0.0               Airport   
5  19.186776  72.859313      Ambewadi             3.0         Women's Store   
6  19.119698  72.846420       Andheri             0.0  Fast Food Restaurant   
7  19.115883  72.854202  Andheri East             0.0     Indian Restaurant   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
3            Coffee Shop                Hostel                  Bank   
4        Airport Service         Jewelry Store           Yoga Studio   
5  Entertainment Service     Indian Restaurant          Dessert Shop   
6             Food Court                Bakery     Indian Restaurant   
7               Gym Pool                 Hotel            Smoke Shop   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
3                Bakery                  Pool          Dessert Shop   
4    Dim Sum Restaurant  Fast Food Restaurant        Farmers Market   
5  Fast Food Restaurant        Farmers Market                  Farm   
6            Restaurant    Dim Sum Restaurant        Farmers Market   
7    Light Rail Station                   Bar     Electronics Store   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
3                  Farm           Event Space  Entertainment Service  
4                  Farm           Event Space  Entertainment Service  
5           Event Space     Electronics Store         Duty-free Shop  
6                  Farm           Event Space  Entertainment Service  
7          Camera Store         Shopping Mall   Gym / Fitness Center

In [53]:
all_merged.dropna(inplace=True)

In [54]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(all_merged['Latitude'],all_merged['Longitude'], all_merged['Neighborhood'], all_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[int(cluster)-1],
        fill=True,
        fill_color=rainbow[int(cluster)-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

## Cluster 1

In [55]:
all_merged.loc[all_merged['Cluster Labels'] == 0, all_merged.columns[[1] + list(range(5, all_merged.shape[1]))]]

Longitude      2nd Most Common Venue          3rd Most Common Venue  \
3    72.824898                Coffee Shop                         Hostel   
4    72.863808            Airport Service                  Jewelry Store   
6    72.846420                 Food Court                         Bakery   
7    72.854202                   Gym Pool                          Hotel   
8    72.846420                 Food Court                         Bakery   
11   72.840038             Ice Cream Shop              Electronics Store   
17   72.833678                  Multiplex                    Yoga Studio   
18   72.832264       Fast Food Restaurant                   Dessert Shop   
20   72.856474                Yoga Studio             Dim Sum Restaurant   
22   72.840432          Electronics Store              Indian Restaurant   
23   72.857363             Clothing Store                     Food Truck   
28   72.825565                Yoga Studio                   Dessert Shop   
29   72.861808                      Hotel                  Design Studio   
32   72.817440                  Juice Bar                    Pizza Place   
35   72.832672                   Platform                  Train Station   
36   72.827340  College Academic Building                       Platform   
37   72.825969             Cosmetics Shop                    Coffee Shop   
38   72.845762                      Plaza                  Train Station   
41   72.842876                      Plaza                  Women's Store   
46   72.860493           Department Store                       Pharmacy   
50   72.844548        Government Building                          Train   
52   72.820791                      Hotel                      Multiplex   
53   72.817908          Indian Restaurant            Indie Movie Theater   
54   72.835284                Yoga Studio                   Dessert Shop   
55   72.850018          Indian Restaurant                           Café   
59   72.810098                       Park                   Concert Hall   
60   72.813573                      Hotel                         Lounge   
70   72.863808            Airport Service                  Jewelry Store   
74   72.864942       Gym / Fitness Center                      BBQ Joint   
75   72.837382        American Restaurant                   Dance Studio   
79   72.826435                 Donut Shop               Asian Restaurant   
80   72.864084       Fast Food Restaurant             Seafood Restaurant   
81   72.842227                        Gym                           Food   
83   72.874835                Yoga Studio                   Dessert Shop   
88   72.852981                Flower Shop                            Gym   
91   72.841534                     Garden  Vegetarian / Vegan Restaurant   
100  72.803366              Design Studio                 Farmers Market   
101  72.848588                   Platform                          Hotel   
104  72.852520         Chinese Restaurant                            Gym   
110  72.838103              Grocery Store              Convenience Store   
117  72.819315                   Platform                     Restaurant   
119  72.834318         Seafood Restaurant           Gym / Fitness Center   
122  72.847871           Department Store                    Yoga Studio   
123  72.823208                Chaat Place              Indian Restaurant   
125  72.823355           Asian Restaurant                 Cricket Ground   
127  72.832264       Fast Food Restaurant                   Dessert Shop   
128  72.815571             Ice Cream Shop                      Juice Bar   
129  72.838966          Indian Restaurant                      Hotel Bar   
130  72.834229                       Café             Chinese Restaurant   
140  72.849538                  Gastropub                      Gift Shop   
143  72.839201               Dessert Shop                    Pizza Place   
149  72.853199       Fast Food Restaurant            

## Cluster 2

In [56]:
all_merged.loc[all_merged['Cluster Labels'] == 1, all_merged.columns[[1] + list(range(5, all_merged.shape[1]))]]

Longitude 2nd Most Common Venue      3rd Most Common Venue  \
176  72.875934           Snack Place  College Academic Building   
5    77.285241          Dessert Shop       Fast Food Restaurant   
36   77.288363   Fried Chicken Joint               Dessert Shop   
53   77.289025    Light Rail Station               Dessert Shop   
70   77.019182          Dessert Shop       Fast Food Restaurant   
71   77.097591             Juice Bar               Dessert Shop   
87   77.105571              Pharmacy                Pizza Place   
161  77.300518          Dessert Shop       Fast Food Restaurant   
221  77.180140  Fast Food Restaurant               Dessert Shop   
271  77.213108   Government Building              Design Studio   
281  77.061882          Dessert Shop       Fast Food Restaurant   
291  77.163475     Mobile Phone Shop       Fast Food Restaurant   
301  77.162658    Light Rail Station                        ATM   
327  77.174137          Dessert Shop       Fast Food Restaurant   
330  77.160629  Fast Food Restaurant               Dessert Shop   
382  77.181251                   ATM               Dessert Shop   
418  77.082305                 Hotel              Design Studio   
468  77.087296         Shopping Mall               Dessert Shop   
469  77.106859          Dessert Shop       Fast Food Restaurant   

    4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
176    Dim Sum Restaurant  Fast Food Restaurant        Farmers Market   
5          Farmers Market                  Farm           Event Space   
36         Farmers Market                  Farm           Event Space   
53         Farmers Market                  Farm           Event Space   
70         Farmers Market                  Farm           Event Space   
71         Farmers Market                  Farm           Event Space   
87          Design Studio                  Farm           Event Space   
161        Farmers Market                  Farm           Event Space   
221        Farmers Market                  Farm           Event Space   
271        Farmers Market                  Farm           Event Space   
281        Farmers Market                  Farm           Event Space   
291    College Auditorium          Concert Hall        Farmers Market   
301       Warehouse Store  Fast Food Restaurant                  Farm   
327        Farmers Market                  Farm           Event Space   
330        Farmers Market                  Farm           Event Space   
382        Farmers Market                  Farm           Event Space   
418        Farmers Market                  Farm           Event Space   
468        Farmers Market                  Farm           Event Space   
469        Farmers Market                  Farm           Event Space   

     7th Most Common Venue  8th Most Common Venue  9th Most Common Venue  \
176                   Farm            Event Space  Entertainment Service   
5    Entertainment Service      Electronics Store         Duty-free Shop   
36   Entertainment Service      Electronics Store         Duty-free Shop   
53   Entertainment Service      Electronics Store         Duty-free Shop   
70   Entertainment Service      Electronics Store         Duty-free Shop   
71   Entertainment Service      Electronics Store         Duty-free Shop   
87   Entertainment Service      Electronics Store         Duty-free Shop   
161  Entertainment Service      Electronics Store         Duty-free Shop   
221  Entertainment Service      Electronics Store         Duty-free Shop   
271  Entertainment Service      Electronics Store         Duty-free Shop   
281  Entertainment Service      Electronics Store         Duty-free Shop   
291                   Farm            Event Space  Entertainment Service   
301            Event Space  Entertainment Service      Electronics Store   
327  Entertainment Service      Electronics Store         Duty-free Shop   
330  Entertainment Service      Electronics Store         Duty-

## Cluster 3

In [57]:
all_merged.loc[all_merged['Cluster Labels'] == 2, all_merged.columns[[1] + list(range(5, all_merged.shape[1]))]]

Longitude   2nd Most Common Venue 3rd Most Common Venue  \
92   77.119360             Yoga Studio         Design Studio   
96   77.030574             Yoga Studio         Design Studio   
129  77.303024  Furniture / Home Store           Yoga Studio   
200  77.185256             Yoga Studio         Design Studio   
256  77.156957             Yoga Studio         Design Studio   

    4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
92         Farmers Market                  Farm           Event Space   
96         Farmers Market                  Farm           Event Space   
129          Dessert Shop        Farmers Market                  Farm   
200        Farmers Market                  Farm           Event Space   
256        Farmers Market                  Farm           Event Space   

     7th Most Common Venue  8th Most Common Venue 9th Most Common Venue  \
92   Entertainment Service      Electronics Store        Duty-free Shop   
96   Entertainment Service      Electronics Store        Duty-free Shop   
129            Event Space  Entertainment Service     Electronics Store   
200  Entertainment Service      Electronics Store        Duty-free Shop   
256  Entertainment Service      Electronics Store        Duty-free Shop   

    10th Most Common Venue  
92     Dumpling Restaurant  
96     Dumpling Restaurant  
129         Duty-free Shop  
200    Dumpling Restaurant  
256    Dumpling Restaurant

## Cluster 4

In [58]:
all_merged.loc[all_merged['Cluster Labels'] == 3, all_merged.columns[[1] + list(range(5, all_merged.shape[1]))]]

Longitude           2nd Most Common Venue          3rd Most Common Venue  \
5    72.859313           Entertainment Service              Indian Restaurant   
9    72.865256                   Grocery Store                          Trail   
16   72.849811              Chinese Restaurant                            Spa   
21   72.837370  Multicuisine Indian Restaurant              Indian Restaurant   
30   72.840800                        Pharmacy  Vegetarian / Vegan Restaurant   
42   72.839427              Chinese Restaurant           Fast Food Restaurant   
47   72.831012                     Coffee Shop                         Lounge   
58   72.832030              Chinese Restaurant              Convenience Store   
63   72.832289                     Pizza Place                   Cupcake Shop   
65   72.830243                          Market                    Cheese Shop   
72   72.834717           Vietnamese Restaurant                      Juice Bar   
73   72.826786                    Cupcake Shop              Indian Restaurant   
78   72.827938                   Jewelry Store                    Yoga Studio   
95   72.827395                    Dessert Shop           Fast Food Restaurant   
97   72.839834                     Bus Station                          Beach   
99   72.839834                     Bus Station                          Beach   
102  72.856318               Indian Restaurant                    Yoga Studio   
105  72.834792                      Smoke Shop             Chinese Restaurant   
106  72.827039                       Bookstore                    Supermarket   
115  72.842890                   Train Station                          Beach   
120  72.852750                     Yoga Studio                  Design Studio   
137  72.856423                       Pet Store                  Train Station   
139  72.838343                      Playground                     Restaurant   
9    77.321516              Light Rail Station              Indian Restaurant   
46   77.290564               Indian Restaurant                  Design Studio   
62   77.030036                     Pizza Place              Indian Restaurant   
80   77.116060            Gym / Fitness Center                         Market   
83   77.286902                       Juice Bar              Indian Restaurant   
104  77.093102               Indian Restaurant                    Yoga Studio   
124  77.236869                          Hostel                          Hotel   
125  77.219843                     Record Shop                         Bakery   
143  77.213005                             Pub              Indian Restaurant   
152  77.261805                  Farmers Market                    IT Services   
154  77.232395               Indian Restaurant                    Yoga Studio   
158  77.220921                  History Museum             Chinese Restaurant   
159  77.220921                  History Museum             Chinese Restaurant   
186  77.274900            Gym / Fitness Center                  Boat or Ferry   
193  77.197626               Indian Restaurant                  Design Studio   
196  77.232194                          Market                    Snack Place   
215  77.120690               Indian Restaurant                    Yoga Studio   
224  77.230552                     Yoga Studio                  Design Studio   
237  77.230853               Indian Restaurant                    Yoga Studio   
242  77.232961                     Snack Place                         Mosque   
254  77.230690                            Park                 Ice Cream Shop   
369  77.136585                     Yoga Studio                  Design Studio   
422  77.204595              Airport Food Court                  Memorial Site   
426  77.125691                      Shoe Store                          Hotel   
459  77.179799                             ATM                         Bakery   
462  77.179122                      

## Cluster 5

In [59]:
all_merged.loc[all_merged['Cluster Labels'] == 4, all_merged.columns[[1] + list(range(5, all_merged.shape[1]))]]

Longitude          2nd Most Common Venue 3rd Most Common Venue  \
14   100.340014              Indian Restaurant                Hostel   
15    72.830267              Indian Restaurant                  Park   
27    72.835335                    Coffee Shop                   Bar   
31    72.825865                         Bakery            Food Truck   
34    72.837053                 Sandwich Place                  Café   
39    72.806538                           Café                Bakery   
43    72.859621                           Café         Train Station   
45    72.825031       Mediterranean Restaurant        Scenic Lookout   
51    72.809547                      Pet Store        Sandwich Place   
71    72.835335                    Coffee Shop                   Bar   
76    72.827528                         Lounge  Gym / Fitness Center   
87    72.844873                           Café        Ice Cream Shop   
93   100.340014              Indian Restaurant                Hostel   
107   72.823781                           Café         Train Station   
109   72.879478                          Hotel           Coffee Shop   
112   72.840012                         Garden                  Café   
114   72.840012                         Garden                  Café   
116   72.840197                            Gym                  Café   
118   72.835335                    Coffee Shop                   Bar   
121   72.880844                            Bar                  Café   
124   72.827956                    Yoga Studio                  Café   
131   72.837661                    Coffee Shop        Sandwich Place   
132   72.839898                    Pizza Place           Snack Place   
134   72.827956                    Yoga Studio                  Café   
141   72.844101                          Hotel         Train Station   
146   72.813990                          Beach                  Farm   
154   72.875170  Vegetarian / Vegan Restaurant           Pizza Place   
164   72.835335                    Coffee Shop                   Bar   
165   72.835335                    Coffee Shop                   Bar   
180   72.816224                 Scenic Lookout                  Café   
59    77.307544                           Bank                  Café   
72    77.096568     Tourist Information Center             Juice Bar   
82    77.087476           Gym / Fitness Center                   Bar   
107   77.107864                    Yoga Studio          Dessert Shop   
126   77.243150                         Market                  Café   
149   77.046691         Furniture / Home Store             Pet Store   
151   77.242969              Indian Restaurant                   Bar   
177   77.226268                         Market                  Café   
198   77.225030             Chinese Restaurant    Light Rail Station   
216   77.194914                    Yoga Studio          Dessert Shop   
225   77.232185              Indian Restaurant                  Café   
227   77.219792                    Coffee Shop     Indian Restaurant   
241   77.249551             Light Rail Station                  Café   
253   77.213031              Indian Restaurant                  Café   
283   77.209941             Miscellaneous Shop                Bakery   
345   77.117074                  Shopping Mall                  Café   
346   77.117074                  Shopping Mall                  Café   
347   77.117074                  Shopping Mall                  Café   
385   77.091106                   Liquor Store         Grocery Store   
401   77.202143                    Pizza Place     Indian Restaurant   
427   77.194447                           Café           Yoga Studio   
428   77.185646                    Coffee Shop                  Café   
454   77.198004             Italian Restaurant                Garden   
489   77.154134                           Café      Business Service   
490   77.154134                           Café

## Conclusion

In this project, we have attempted to load the dataset for two of India’s prime metro cities and have tried to analyze the neighborhood regions in these metro cities based on the type of popular and top venues they have. We have clustered the neighborhoods based on the most common top venues in each of the neighborhood. Our intention with this project was to analyze and understand the similarity in the type of life in these metros, which can offer decision points for anybody who is considering to settle in either of the metro cities and can get a peek into what type of experience and facilities he will be provided with.

Given our cluster information for both Mumbai and Delhi, we see that Mumbai and its neighbourhoods are a great place for a foodie. There are a lot of restaurants, cafes, bars, etc in Mumbai neighbourhoods. Also due to the proximity of Mumbai to the seashore, Mumbai neighborhoods offer for harbors, seafood, boat, and ferry rides. On the other hand, we see how dissimilar life in Delhi neighbourhoods would be compared to Mumbai neighbourhoods. Delhi neighborhoods and good for those who like Arts and Crafts, Museums, Water Parks and Pizza places. There is very less in terms of foreign cuisine restaurants in Delhi. Mumbai, on the other hand, is great for international visitors, expats, etc, because of the variety and types of food outlets it has. Delhi is inland and its neighborhoods have proximity to Water Parks, Museums and Arts, and Crafts stores.

Thus with this project, we have analyzed the kind of life each of these big metro cities has to offer based on the popular venues in their neighborhood.